In [23]:
import copy

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import lime
import lime.lime_tabular
import support_functions as sf

import shap

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score
from sklearn.dummy import DummyClassifier
from sklearn.svm import SVC
from sklearn.neighbors import NearestNeighbors

from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn import tree


from scipy.stats import multivariate_normal

import copy
# sharp plots with higher resolution
%config InlineBackend.figure_format = 'svg'
plt.rcParams['figure.dpi'] = 150
plt.rcParams['savefig.dpi'] = 150

In [11]:
def gaussian_generator(center, eig_val, eig_vec, size):
    sigma = np.matmul(np.matmul(eig_vec, eig_val), np.transpose(eig_vec))
    data_set = np.random.multivariate_normal(center, sigma, size)

    return data_set, sigma

In [13]:
# alternative data set
n_1 = 1000  # number of the elements
mu_1 = np.array([0, 0])  # center (centroid)

# sigma is expected to be positive  semi-definite matrix
w_1 = np.array([[1.5, 0], [0, 4.5]])  # eigenvalues
v_1 = np.array([[0.4, 0], [0, 0.4]])  # eigenvectors

set_1, sigma_1 = gaussian_generator(mu_1,w_1, v_1, n_1)

set_1_1 = set_1[set_1[:, 0] > 0.5, :]
set_1_2 = set_1[set_1[:, 0] < 0.5, :]

set_1_3 = set_1_1[set_1_1[:, 1] < -0.5, :]
set_1_1 = set_1_1[set_1_1[:, 1] > -0.5, :]
set_1_4 = set_1_2[set_1_2[:, 1] < -0.5, :]
set_1_2= set_1_2[set_1_2[:, 1] > -0.5, :]

set_2_1 = set_1_1
set_2_2 = set_1_2
set_2_3 = set_1_3
set_2_4 = set_1_4

set_2_1 = set_2_1
set_2_2[:, 0] = set_2_2[:, 0] - 0.1
set_2_2[:, 1] = set_2_2[:, 1] + 0.1
set_2_4 = set_2_4
set_2_3[:, 0] = set_2_3[:, 0]
set_2_3[:, 1] = set_2_3[:, 1]

class_9 = set_2_2
class_10 = np.vstack([set_2_1, set_2_3, set_2_4])

labels_9 = np.zeros((len(class_9), 1))
labels_10 = np.ones((len(class_10), 1))

class_9 = np.hstack([class_9, labels_9])
class_10 = np.hstack([class_10, labels_10])

data_set_norm_hm_sq = np.vstack([class_9, class_10])
np.random.shuffle(data_set_norm_hm_sq)

data_set_norm_hm_sq = data_set_norm_hm_sq[data_set_norm_hm_sq[:, 0] < 2, :]
data_set_norm_hm_sq = data_set_norm_hm_sq[data_set_norm_hm_sq[:, 0] > -2, :]

data_set_norm_hm_sq = data_set_norm_hm_sq[data_set_norm_hm_sq[:, 1] < 2, :]

In [14]:
data_set = data_set_norm_hm_sq.copy()
data_set_0 = data_set[data_set[:, -1] == 0]
data_set_1 = data_set[data_set[:, -1] == 1]

In [15]:
X = data_set[:, 0:2].copy()
y = data_set[:, 2].copy()

In [17]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1, test_size=0.3, train_size=0.7)

In [18]:
clf_svc = SVC(kernel='rbf', probability=True)
clf_tree = tree.DecisionTreeClassifier()
clf_KNN = KNeighborsClassifier()
clf_GNB = GaussianNB()

In [20]:
explainer_lime = lime.lime_tabular.LimeTabularExplainer(training_data=X_train, feature_names=["feat1","feat2"],
                                                  class_names=["class1","class2"], mode='classification',
                                                discretize_continuous=False)

In [21]:
flat_grid, grid_elements  = sf.get_grid(data_set=X_test, step_size=0.04, idx_column=False)

In [22]:
y_hat, hat_grid, exp_grid_weights = sf.classify_and_explain(X_train, X_test, y_train, y_test, flat_grid, classifier=clf_svc, explainer=explainer_lime, data_name='Original', print_metrics=True)

Original   <class 'sklearn.svm._classes.SVC'>  accuracy score:  0.9932885906040269
Original   <class 'sklearn.svm._classes.SVC'>  precision score:  1.0
Original   <class 'sklearn.svm._classes.SVC'>  recall score:  0.9824561403508771
Original   <class 'sklearn.svm._classes.SVC'>  f1 score:  0.9911504424778761
Using:  <lime.lime_tabular.LimeTabularExplainer object at 0x000001E2AB9227D0>
lime


In [24]:
n_grid = len(hat_grid)
pdf_val = np.zeros((n_grid, 1))
for i in range(0, n_grid):
    pdf_val[i, 0] = multivariate_normal.pdf(flat_grid[i, :], mu_1, sigma_1)

In [35]:
plt.rcParams['figure.figsize'] = [10, 10]
fig_1, (ax_11, ax_12, ax_13) = plt.subplots(1,3, layout='constrained')
plt.subplot(131)
plt.title('voting of the first feature')
ax_11.scatter(flat_grid[:, 0], flat_grid[:, 1], c= exp_grid_weights[:, 0], cmap='RdBu', s=10, alpha=0.7)
ax_11.set_aspect('equal')
plt.subplot(132)

plt.title('voting of the second feature')
ax_12.scatter(flat_grid[:, 0], flat_grid[:, 1], c= exp_grid_weights[:, 1], cmap='RdBu', s=10, alpha=0.7)
ax_12.set_aspect('equal')
plt.subplot(133)
plt.title('data PDF plot')
ax_13.scatter(flat_grid[:, 0], flat_grid[:, 1], c= pdf_val[:, 0], cmap='Greys', s=10, alpha=0.7)
ax_13.set_aspect('equal')
plt.show

<function matplotlib.pyplot.show(close=None, block=None)>